In [1]:
import tensorflow as tf
import tensorflow_hub as hub
import numpy as np
import tensorflow_text
import tqdm
questions = ["What is your age?"]
responses = ["I am 20 years old.", "good morning"]
response_contexts = ["I will be 21 next year.", "great day."]

module = hub.load('https://tfhub.dev/google/universal-sentence-encoder-multilingual-qa/3')

question_embeddings = module.signatures['question_encoder'](
            tf.constant(questions))


response_embeddings = module.signatures['response_encoder'](
        input=tf.constant(responses),
        context=tf.constant(response_contexts))

np.inner(question_embeddings['outputs'], response_embeddings['outputs'])


array([[0.40883988, 0.08877401]], dtype=float32)

In [2]:
import os
from tqdm import tqdm
import pandas as pd

In [3]:
response_embeddings = module.signatures['response_encoder'](
input=tf.constant(responses),
context=tf.constant(response_contexts))

In [4]:
data_folder = 'data/'
url_doc_file = data_folder + "urls.numerate.txt"
content_folder = data_folder + 'content/'

In [5]:
content_folder = data_folder + 'content/'
urls_dict = dict() #url - header

#list with document objects
documents = []
#list with documents which urls are absent in urls.numerate.txt
errors = []
absent_doc_files = []

i = 0

for folder_path in tqdm(os.listdir(content_folder)):
    filepath = content_folder + folder_path + '/'
    #print(os.listdir(filepath))
    for fname in os.listdir(filepath):
        i += 1
        #print(fname)
        f = open(filepath + fname, "r", encoding="utf-8", errors='replace')
        url = f.readline()[:-1]
        for line in f:
            if '<title>' in line:
                a = line.find('</title>')
                b = line.find('<title>')
                if url in urls_dict:
                    #print(urls_dict[url], line[len('<title>'):a])
                    #break
                    urls_dict[url].append(line[b + len('<title>'):a])
                    #print(1)
                else:
                    urls_dict[url] = line[b + len('<title>'):a]
                break
        f.close()

100%|██████████| 8/8 [00:14<00:00,  1.83s/it]


In [9]:
urls_dict.values()

dict_values(['Стена | ВКонтакте', 'Автомобильное мультимедийное устройство на ОС Android &bull; Российский клуб любителей Toyota Wish (Тойота Виш)', 'Комментарии к Honda Accord Coupe Моя малышка)))', ' XL CVT - вопросы по работе и эксплуатация вариатора 2.4 - Page 99 - OUT-CLUB.RU', 'Содержание курса 9 класса - Литература', ' Топ 10 Самые лучшие сериалы в мире', 'реп скажи - слушать онлайн, быстро скачать без смс в mp3 формате на нашей поисковой системе', 'Расширение экрана в GTA 5 :: Grand Theft Auto V Общие обсуждения', 'Длина штор зависит от высоты комнаты. Всё о том, какой длины должны быть шторы.', 'ЭКСМО &bull; Просмотр темы - Виртронация, роман, научная фантастика', 'Как потолстеть подростку? | Домашний способ', 'Рисуем черепа - Аэрография для всех', 'Стена | ВКонтакте', 'Перевязка труб у женщин: последствия. Какими могут быть последствия перевязки труб?', 'Анализ состояния ресурсов и степень их использования  в МБУК «Гаврилов-Ямская межпоселенческая центральная  районная библио

In [6]:
sumbission_file = 'data/sample.technosphere.ir1.textrelevance.submission.txt'
queries_file = 'data/queries.numerate.txt'
urls_file = 'data/urls.numerate.txt'

In [7]:
nums_urls_dict = dict()
with open(urls_file) as ur_file:
    i = 1
    for line in ur_file:
        #print(line)
        data = line.strip('\n').split('\t')
        if i == 120:
            print(data)
        nums_urls_dict[int(data[0])] = data[1]
        i += 1
        #print(data)

['120', 'facebook.com/pages/%D0%A2%D1%83%D1%80%D0%BC%D0%B0%D0%BB%D0%B8%D0%BD%D0%BE%D0%B2%D0%B0%D1%8F-%D0%BF%D1%80%D0%BE%D0%B4%D1%83%D0%BA%D1%86%D0%B8%D1%8F/294560463970429']


In [8]:
from spellchecker import SpellChecker
from pymystem3 import Mystem
spell = SpellChecker(language='en')

In [9]:
spell.correction('I lovid hame')

'I lovid hame'

In [10]:
queries_dict = dict()
with open(queries_file) as ur_file:
    i = 1
    for line in ur_file:
        #print(line)
        data = line.strip('\n').split('\t')
        #queries_dict[int(data[0])] = ''.join(obj.lemmatize(data[1].lower())[:-1])
        queries_dict[int(data[0])] = data[1].lower()
        #print(data)

In [11]:
sumbission_file

'data/sample.technosphere.ir1.textrelevance.submission.txt'

In [12]:
baseline_file = 'baseline.txt'

In [13]:
sumbission_dict = dict()
with open(baseline_file) as sub_file:
    i = 0
    for line in sub_file:
        if i > 0:
            #print(line)
            data = line.strip('\n').split(',')
            n = int(data[0])
            num = int(data[1])
            if n in sumbission_dict:
                sumbission_dict[n].append(num)
            else:
                sumbission_dict[n] = [num]
            #print(data)
        i += 1

In [ ]:
out_file = open("myfile.json", "w") 
  
json.dump(dict1, out_file, indent = 6) 
  
out_file.close() 

In [16]:
import json

In [20]:
with open('queries_dict.json', 'w') as f:
    json.dump(queries_dict, f)

In [21]:
with open('sumbission_dict.json', 'w') as f:
    json.dump(sumbission_dict, f)

In [22]:
with open('nums_urls_dict.json', 'w') as f:
    json.dump(nums_urls_dict, f)

In [23]:
with open('urls_dict.json', 'w') as f:
    json.dump(urls_dict, f)

In [22]:
np.argsort(list(queries_dict.keys()))[::-1]

array([398, 397, 396, 395, 394, 393, 392, 391, 390, 389, 388, 387, 386,
       385, 384, 383, 382, 381, 380, 379, 378, 377, 376, 375, 374, 373,
       372, 371, 370, 369, 368, 367, 366, 365, 364, 363, 362, 361, 360,
       359, 358, 357, 356, 355, 354, 353, 352, 351, 350, 349, 348, 347,
       346, 345, 344, 343, 342, 341, 340, 339, 338, 337, 336, 335, 334,
       333, 332, 331, 330, 329, 328, 327, 326, 325, 324, 323, 322, 321,
       320, 319, 318, 317, 316, 315, 314, 313, 312, 311, 310, 309, 308,
       307, 306, 305, 304, 303, 302, 301, 300, 299, 298, 297, 296, 295,
       294, 293, 292, 291, 290, 289, 288, 287, 286, 285, 284, 283, 282,
       281, 280, 279, 278, 277, 276, 275, 274, 273, 272, 271, 270, 269,
       268, 267, 266, 265, 264, 263, 262, 261, 260, 259, 258, 257, 256,
       255, 254, 253, 252, 251, 250, 249, 248, 247, 246, 245, 244, 243,
       242, 241, 240, 239, 238, 237, 236, 235, 234, 233, 232, 231, 230,
       229, 228, 227, 226, 225, 224, 223, 222, 221, 220, 219, 21

In [14]:
for i in urls_dict.values():
    if len(i) > 2500:
        print('!')

In [15]:
from copy import deepcopy

In [16]:
def make_ans(mode = 'baseline', part = 20):
    ans = dict()

    for i in tqdm(range(1, 400), leave=False):
        query = queries_dict[i]
        if mode == 'baseline':
            url_nums = deepcopy(sumbission_dict[i][:part])
        else:
            url_nums = deepcopy(sumbission_dict[i])
        titles_by_nums = []
        for j in url_nums:
            tmp = nums_urls_dict[j]
            if tmp in urls_dict:
                titles_by_nums.append(urls_dict[tmp][:2500])
            else:
                titles_by_nums.append('urls_dict[tmp]')

        #print(len(titles_by_nums))
        step = 20
        ind = step

        tmp = []
        while ind <= len(titles_by_nums):
            question_embeddings = module.signatures['question_encoder'](
                    tf.constant(query))


            response_embeddings = module.signatures['response_encoder'](
                    input=tf.constant(titles_by_nums[ind - step: ind]),
                    context=tf.constant(titles_by_nums[ind - step: ind]))
            #print(np.inner(question_embeddings['outputs'], response_embeddings['outputs'])[0])
            tmp += list(np.inner(question_embeddings['outputs'], response_embeddings['outputs'])[0])
            ind += step
        url_nums = np.array(url_nums)
        if mode == 'baseline':
            baseline = deepcopy(sumbission_dict[i])
            #print(len(tmp))
            #print(baseline[:20], url_nums[np.argsort(tmp)])
            baseline[:part] = url_nums[np.argsort(tmp)][::-1]
            #print(baseline[:20])
            ans[i] = baseline
        else:
            ans[i] = url_nums[np.argsort(tmp)][::-1]
    return ans

In [25]:
ans = make_ans(part = 40)

In [74]:
ans = dict()

for i in tqdm(range(1, 400), leave=False):
    query = queries_dict[i]
    url_nums = sumbission_dict[i]
    titles_by_nums = []
    for j in url_nums:
        tmp = nums_urls_dict[j]
        if tmp in urls_dict:
            titles_by_nums.append(urls_dict[tmp][:2500])
        else:
            titles_by_nums.append('urls_dict[tmp]')
    
    
    step = 20
    ind = step
    
    tmp = []
    while ind < len(titles_by_nums):
        question_embeddings = module.signatures['question_encoder'](
                tf.constant(query))


        response_embeddings = module.signatures['response_encoder'](
                input=tf.constant(titles_by_nums[ind - step: ind]),
                context=tf.constant(titles_by_nums[ind - step: ind]))
        #print(np.inner(question_embeddings['outputs'], response_embeddings['outputs'])[0])
        tmp += list(np.inner(question_embeddings['outputs'], response_embeddings['outputs'])[0])
        ind += step
    url_nums = np.array(url_nums)
    ans[i] = url_nums[np.argsort(tmp)][::-1]
    

In [22]:
final_ans = []
for num in ans.keys():
    docs = ans[num]
    for i in docs:
        final_ans.append([num, i])

In [23]:
sumbission_dict[1][:20]

[78, 28, 74, 53, 44, 82, 7, 85, 57, 54, 51, 68, 88, 67, 70, 83, 66, 62, 39, 73]

In [24]:
pd.DataFrame(final_ans, columns=['QueryId', 'DocumentId']).to_csv('subm12.csv', index=False)

In [158]:
data = pd.read_csv('subm10.csv')
data.head(20)

QueryId  DocumentId
0         1          74
1         1          28
2         1          53
3         1           7
4         1          78
5         1          57
6         1          66
7         1          51
8         1          85
9         1          70
10        1          68
11        1          83
12        1          44
13        1          67
14        1          82
15        1          88
16        1          54
17        1          73
18        1          62
19        1          39

In [119]:
data = pd.read_csv('subm7.csv')
data.head(20)

QueryId  DocumentId
0         1          74
1         1          53
2         1          78
3         1          28
4         1           7
5         1          57
6         1          58
7         1          60
8         1          66
9         1          70
10        1          51
11        1          44
12        1          68
13        1          67
14        1          75
15        1          24
16        1          18
17        1          77
18        1          61
19        1          17

In [114]:
'facebook.com/pages/%D0%A2%D1%83%D1%80%D0%BC%D0%B0%D0%BB%D0%B8%D0%BD%D0%BE%D0%B2%D0%B0%D1%8F-%D0%BF%D1%80%D0%BE%D0%B4%D1%83%D0%BA%D1%86%D0%B8%D1%8F/294560463970429' in urls_dict

False

In [101]:
with open(sumbission_file) as sub_file:
    i = 0
    for line in sub_file:
        if i > 0:
            print(line)
            
            #print(data)
        i += 1

1,1

1,2

1,3

1,4

1,5

1,6

1,7

1,8

1,9

1,10

1,11

1,12

1,13

1,14

1,15

1,16

1,17

1,18

1,19

1,20

1,21

1,22

1,23

1,24

1,25

1,26

1,27

1,28

1,29

1,30

1,31

1,32

1,33

1,34

1,35

1,36

1,37

1,38

1,39

1,40

1,41

1,42

1,43

1,44

1,45

1,46

1,47

1,48

1,49

1,50

1,51

1,52

1,53

1,54

1,55

1,56

1,57

1,58

1,59

1,60

1,61

1,62

1,63

1,64

1,65

1,66

1,67

1,68

1,69

1,70

1,71

1,72

1,73

1,74

1,75

1,76

1,77

1,78

1,79

1,80

1,81

1,82

1,83

1,84

1,85

1,86

1,87

1,88

1,89

1,90

1,91

1,92

1,93

1,94

1,95

1,96

2,97

2,98

2,99

2,100

2,101

2,102

2,103

2,104

2,105

2,106

2,107

2,108

2,109

2,110

2,111

2,112

2,113

2,114

2,115

2,116

2,117

2,118

2,119

2,120

2,121

2,122

2,123

2,124

2,125

2,126

2,127

2,128

2,129

2,130

2,131

2,132

2,133

2,134

2,135

2,136

2,137

2,138

2,139

2,140

2,141

2,142

2,143

2,144

2,145

2,146

2,147

2,148

2,149

2,150

2,151

2,152

2,153

2,154

2,155

2,156

2,157

2,158

2,

34,3314

34,3315

34,3316

34,3317

34,3318

34,3319

34,3320

34,3321

34,3322

34,3323

34,3324

34,3325

34,3326

34,3327

34,3328

34,3329

34,3330

34,3331

34,3332

34,3333

34,3334

34,3335

34,3336

34,3337

34,3338

34,3339

34,3340

34,3341

34,3342

34,3343

34,3344

34,3345

34,3346

34,3347

34,3348

34,3349

34,3350

34,3351

34,3352

34,3353

34,3354

34,3355

34,3356

34,3357

34,3358

34,3359

34,3360

34,3361

35,3362

35,3363

35,3364

35,3365

35,3366

35,3367

35,3368

35,3369

35,3370

35,3371

35,3372

35,3373

35,3374

35,3375

35,3376

35,3377

35,3378

35,3379

35,3380

35,3381

35,3382

35,3383

35,3384

35,3385

35,3386

35,3387

35,3388

35,3389

35,3390

35,3391

35,3392

35,3393

35,3394

35,3395

35,3396

35,3397

35,3398

35,3399

35,3400

35,3401

35,3402

35,3403

35,3404

35,3405

35,3406

35,3407

35,3408

35,3409

35,3410

35,3411

35,3412

35,3413

35,3414

35,3415

35,3416

35,3417

35,3418

35,3419

35,3420

35,3421

35,3422

35,3423

35,3424

3

73,6912

73,6913

73,6914

73,6915

73,6916

73,6917

73,6918

73,6919

73,6920

73,6921

73,6922

73,6923

73,6924

73,6925

73,6926

73,6927

73,6928

73,6929

73,6930

73,6931

73,6932

73,6933

73,6934

73,6935

73,6936

73,6937

73,6938

73,6939

73,6940

73,6941

73,6942

73,6943

73,6944

73,6945

73,6946

73,6947

73,6948

73,6949

73,6950

73,6951

73,6952

73,6953

73,6954

73,6955

73,6956

73,6957

73,6958

73,6959

73,6960

73,6961

73,6962

73,6963

73,6964

73,6965

73,6966

73,6967

73,6968

73,6969

73,6970

73,6971

73,6972

73,6973

73,6974

73,6975

73,6976

73,6977

73,6978

73,6979

73,6980

73,6981

73,6982

73,6983

73,6984

73,6985

73,6986

73,6987

73,6988

73,6989

73,6990

73,6991

73,6992

73,6993

73,6994

73,6995

73,6996

73,6997

73,6998

73,6999

73,7000

73,7001

74,7002

74,7003

74,7004

74,7005

74,7006

74,7007

74,7008

74,7009

74,7010

74,7011

74,7012

74,7013

74,7014

74,7015

74,7016

74,7017

74,7018

74,7019

74,7020

74,7021

74,7022

7

109,10422

109,10423

109,10424

109,9096

109,10425

109,10426

109,10427

109,10428

109,10429

109,10430

109,10431

109,10432

109,10433

109,10434

109,10435

109,10436

109,10437

109,10438

109,10439

109,10440

109,10441

109,10442

109,10443

109,10444

109,10445

109,10446

109,10447

109,10448

109,10449

109,10450

109,10451

109,10452

109,10453

109,10454

109,10455

109,10456

109,10457

109,10458

109,10459

109,10460

109,10461

109,10462

109,10463

109,10464

109,8265

109,10465

109,10466

109,10467

109,10468

109,10469

109,10470

109,10471

109,10472

109,10473

109,10474

109,10475

109,10476

109,10477

109,10478

109,10479

109,10480

109,10481

109,10482

109,10483

109,10484

109,10485

109,10486

109,10487

109,10488

109,10489

109,10490

109,10491

109,10492

109,10493

109,10494

109,10495

109,10496

109,10497

109,10498

109,10499

109,10500

109,10501

109,10502

109,10503

109,10504

109,10505

109,10506

109,10507

109,10508

109,10509

109,10510

1

145,13984

145,13985

145,13986

145,13987

145,13988

145,13989

145,13990

145,13991

145,13992

145,13993

145,13994

145,9866

145,13995

145,13996

145,13997

145,13998

145,13999

145,14000

145,14001

145,14002

145,14003

145,14004

145,14005

145,14006

145,14007

145,14008

145,14009

145,14010

145,14011

145,14012

145,14013

145,14014

145,3999

145,14015

145,14016

145,14017

145,6783

145,14018

145,14019

145,14020

145,14021

145,14022

145,14023

145,14024

145,14025

145,14026

145,14027

145,14028

145,14029

145,14030

145,14031

145,14032

145,14033

145,14034

146,14035

146,14036

146,14037

146,14038

146,14039

146,14040

146,14041

146,14042

146,14043

146,14044

146,14045

146,14046

146,14047

146,14048

146,14049

146,14050

146,14051

146,14052

146,14053

146,14054

146,14055

146,14056

146,14057

146,14058

146,14059

146,14060

146,14061

146,14062

146,14063

146,14064

146,14065

146,14066

146,14067

146,14068

146,14069

146,14070

146,14071

14

...


219,21089

219,21090

219,3862

219,21091

219,21092

219,21093

219,21094

219,21095

219,21096

219,21097

219,21098

219,21099

219,21100

219,21101

219,21102

219,21103

219,21104

219,21105

219,21106

219,21107

219,21108

219,21109

219,21110

219,21111

219,21112

219,21113

219,21114

219,21115

219,21116

219,21117

219,21118

219,21119

219,21120

219,21121

219,21122

219,21123

219,21124

219,21125

219,21126

219,21127

219,21128

219,21129

219,21130

220,21131

220,21132

220,21133

220,21134

220,21135

220,21136

220,21137

220,21138

220,21139

220,21140

220,21141

220,21142

220,21143

220,21144

220,21145

220,21146

220,21147

220,21148

220,21149

220,21150

220,21151

220,21152

220,21153

220,21154

220,21155

220,21156

220,21157

220,21158

220,21159

220,21160

220,21161

220,21162

220,21163

220,21164

220,21165

220,21166

220,21167

220,21168

220,21169

220,21170

220,21171

220,21172

220,21173

220,21174

220,21175

220,21176

220,21177

220,21178


257,24579

257,24580

257,24581

257,24582

257,24583

257,24584

257,24585

257,24586

257,24587

257,24588

257,24589

257,24590

257,24591

257,24592

257,24593

257,24594

257,24595

257,24596

257,24597

257,24598

257,24599

257,24600

257,24601

257,24602

257,24603

257,24604

257,24605

257,24606

257,24607

257,24608

257,24609

257,24610

257,24611

257,24612

257,2911

257,24613

257,24614

257,24615

257,24616

257,4167

257,24617

257,24618

257,24619

257,24620

257,24621

257,24622

257,24623

257,24624

257,24625

257,24626

257,24627

257,24628

257,24629

257,24630

257,24631

257,24632

257,24633

257,24634

257,24635

257,24636

257,24637

257,24638

257,24639

257,24640

257,24641

257,24642

257,24643

257,24644

257,24645

257,24646

257,24647

257,24648

257,24649

257,24650

257,24651

257,24652

257,24653

257,24654

257,24655

257,24656

257,24657

257,24658

257,24659

257,24660

257,24661

257,24662

257,24663

257,24664

257,24665

257,24666

257,24667

2

295,28187

295,28188

295,28189

295,28190

295,28191

295,28192

295,28193

295,28194

295,28195

295,28196

295,28197

295,28198

295,28199

295,28200

295,28201

295,28202

295,28203

295,28204

295,28205

295,28206

295,28207

295,28208

295,28209

295,28210

295,28211

295,28212

295,28213

295,28214

295,28215

295,28216

295,28217

295,28218

295,28219

295,28220

295,28221

295,28222

295,28223

295,28224

295,28225

295,28226

295,28227

295,28228

295,28229

295,28230

295,28231

295,28232

295,28233

295,28234

295,28235

295,28236

295,28237

295,28238

295,28239

295,28240

295,28241

295,28242

295,28243

295,28244

295,28245

295,28246

295,28247

295,28248

295,28249

295,28250

295,28251

295,28252

295,28253

295,28254

295,28255

295,28256

295,28257

295,28258

295,28259

295,28260

295,28261

295,28262

295,28263

295,28264

295,28265

295,28266

295,28267

295,28268

295,28269

295,28270

295,28271

296,28272

296,28273

296,28274

296,28275

296,28276

296,28277



332,31755

332,31756

332,31757

332,31758

332,31759

332,31760

332,31761

332,31762

332,31763

332,31764

332,31765

332,31766

332,31767

332,31768

332,31769

332,31770

332,31771

332,31772

332,31773

332,31774

332,31775

332,31776

332,31777

332,31778

332,31779

332,31780

332,31781

332,31782

332,31783

332,31784

332,31785

332,31786

332,31787

332,31788

332,31789

332,31790

332,31791

332,31792

332,31793

332,31794

332,31795

332,31796

332,31797

332,31798

332,31799

332,31800

332,31801

332,3167

332,31802

332,31803

332,31804

332,31805

332,31806

332,31807

332,31808

332,31809

332,31810

332,31811

332,31812

332,31813

332,31814

332,31815

332,31816

332,31817

332,31818

332,31819

332,31820

332,31821

332,31822

332,31823

332,31824

332,31825

333,31826

333,31827

333,31828

333,31829

333,31830

333,31831

333,31832

333,31833

333,31834

333,31835

333,31836

333,31837

333,31838

333,31839

333,31840

333,31841

333,31842

333,31843

333,10505



371,35395

371,35396

371,35397

371,35398

371,35399

371,35400

371,35401

371,35402

371,35403

371,35404

371,35405

371,35406

371,35407

371,35408

371,35409

371,35410

371,35411

371,35412

371,35413

371,35414

371,35415

371,35416

371,35417

371,35418

371,35419

371,35420

371,35421

371,35422

371,35423

371,35424

371,35425

371,35426

371,35427

371,35428

371,35429

371,35430

371,35431

371,35432

371,35433

371,35434

371,35435

371,35436

371,35437

371,35438

371,35439

371,35440

371,35441

371,35442

371,35443

371,35444

371,35445

371,35446

371,35447

371,35448

371,35449

371,35450

371,35451

371,35452

371,35453

371,35454

371,35455

371,35456

371,35457

371,35458

371,35459

371,35460

371,35461

371,35462

371,35463

371,35464

371,35465

371,35466

371,35467

371,35468

371,35469

371,35470

371,35471

371,35472

371,35473

371,35474

371,35475

371,35476

371,35477

371,35478

371,35479

371,35480

371,35481

371,35482

371,35483

371,35484

371,35485